# Air Temperature and Precipitation

In this section we'll look at air temperature and precipitation in the Lower Capilano Watershed for 2023, and compare these values to historical conditions. The winter season was generally cooler than average (as is common during La Nina seasons), and saw near-normal precipitation and snowpack. Conditions changed abruptly near the end of April. This spring and summer have been hot and exceptionally dry.   

The maps below show the monthly temperature anomaly and percent of normal precipitation for Western Canada in June, 2023. June was a warm and dry month, right on the heels of a very hot and dry May.

```{figure} img/june_temp_anom.png
---
height: 350px
name: temp_map
---
June Temperature Anomaly for Western Canada
```

```{figure} img/june_precip_percent.png
---
height: 350px
name: precip_map
---
June Percent of Normal Precipitation for Western Canada
```

The table below shows monthly air temperature and precipitation data for the Lower Capilano Watershed. May is certainly a standout month with average temperatures almost 4 degrees warmer than normal, combined only 15% of normal precipitation. 

| **Month** | Mean Temp | Temp Anomaly | Precip | Precip % Normal |
| -  | - | - |  - | - |
| **January** | 3.5 | +0.4  | 318 | 87 |
| **February** | 1.8 | -1.0 | 333 | 145 |
| **March** | 4.2 | -0.6 | 118 | 35 |
| **April** | 6.2 | -1.2 | 315 | 159 |
| **May** |  15.4 | **+3.7** | 19 | **15** |
| **June** | 16.5 | +1.3 | 48 | 45 |
| **July** | 19.6 | +1.5 | 8 | 22 |


In [1]:
# Import libraries
import pandas as pd
import os
import numpy as np
import matplotlib.pyplot as plt
import altair as alt
import altair_saver 

In [15]:

os.chdir('C://Users/pmarshal/Documents/Climate-Outlook/monthly-climate')
os.getcwd()

'C:\\Users\\pmarshal\\Documents\\Climate-Outlook\\monthly-climate'

In [16]:
# Import dataset
temp = pd.read_csv('data/QD1_temps.csv', parse_dates=['date']) 
temp['year'] = pd.DatetimeIndex(temp['date']).year
temp['month'] = pd.DatetimeIndex(temp['date']).month
temp['day'] = pd.DatetimeIndex(temp['date']).day
temp['DOY'] = pd.DatetimeIndex(temp['date']).dayofyear

In [30]:
# Claculate statistics on mean temp column
temp['mean'] = temp.groupby('DOY')['mean_TA'].transform('mean')
temp['max'] = temp.groupby('DOY')['mean_TA'].transform('max')
temp['min'] = temp.groupby('DOY')['mean_TA'].transform('min')
temp['std'] = temp.groupby('DOY')['mean_TA'].transform('std')
temp['sem'] = temp.groupby('DOY')['mean_TA'].transform('sem')
temp['ci95_hi'] = temp['mean'] + 1.96* temp['sem']
temp['ci95_lo'] = temp['mean'] - 1.96* temp['sem']


In [18]:
# Create dataframe with data for the current year
current_year = temp.loc[temp['year'] == 2023]

In [19]:
# Create dataframe with historical data (i.e. not == current year)
past = temp.loc[temp['year'] != 2023]

In [20]:
past_stats = past.loc[0:364]

In [21]:
# Calculate past low temperatures
pastlow = past.groupby('DOY')['mean_TA'].transform('min')
pastlow = pastlow.reset_index()
pastlow = pastlow.loc[0:364]
pastlow['DOY'] = past['DOY']
pastlow = pastlow.rename(columns={"mean_TA": "low"})

In [22]:
# Calculate past high temperatures
pasthigh = past.groupby('DOY')['mean_TA'].transform('max')
pasthigh = pasthigh.reset_index()
pasthigh = pasthigh.loc[0:364]
pasthigh['DOY'] = past['DOY']
pasthigh = pasthigh.rename(columns={"mean_TA": "high"})

In [23]:
# Calculate new lows this year
present_low = pd.merge(current_year, pastlow)
present_low = present_low[present_low['mean_TA'] <= present_low['low']]

In [29]:
# Calculate new highs this year
present_high = pd.merge(current_year, pasthigh)
present_high = present_high[present_high['mean_TA'] >= present_high['high']]


In [25]:
plot_2023 = alt.Chart(current_year).mark_line(color='darkred', strokeWidth=1.5).encode(
    alt.X('monthdate(date)'),
    alt.Y('mean_TA'),
    tooltip=[alt.Tooltip('monthdate(date):T', title="Date"), alt.Tooltip('mean_TA:Q', title="Air Temp")]
)

plot_lows = alt.Chart(present_low).mark_circle(color='blue', size=40).encode(
    alt.X('monthdate(date)'),
    alt.Y('mean_TA')
)

plot_highs = alt.Chart(present_high).mark_circle(color='red', size=40).encode(
    alt.X('monthdate(date)'),
    alt.Y('mean_TA')
)

plot_current = plot_2023 + plot_lows + plot_highs
plot_current

alt.LayerChart(...)

## Air Temperatures

The plot below shows the average daily temperature for 2023 (red line) compared to normals (gray shaded area) and the range of max and min (blue shaded area). New high and low temperature records are also plotted with red and blue dots. The sudden change in temperatures at the end of April is very clear. Nine new daily temperature records were set in May alone. 

In [26]:
title = alt.TitleParams(
   text='Lower Capilano Watershed',
   subtitle="Mean Daily Temperature",
   anchor='middle',
   fontSize=14,
   fontWeight='bold')

area = alt.Chart(past_stats, title=title).mark_area(color='#7DA6F3', opacity=0.5).encode(
    alt.X('monthdate(date)', title=' '),
    alt.Y('max:Q', title='Air Temperature (C)'),
    alt.Y2('min:Q')
).properties(width=600, height=300)

area2 = alt.Chart(past_stats).mark_area(color='#919397', opacity=0.6).encode(
    alt.X('monthdate(date)'),
    alt.Y('ci95_hi:Q'),
    alt.Y2('ci95_lo:Q')
)
area + area2 + plot_current.interactive()

alt.LayerChart(...)

```{admonition} **Hottest Day of the year**
:class: attention
The hottest recorded temperature so far this year was on **May 15th**. The daytime high reached **32.7** degrees in the lower Capilano Watershed
```

## Precipitation

The plot below shows the accumulated precipitation in the Lower Capilano Watershed in 2023. Last year is also shown in dark blue, and other years between 2003 and 2021 are shown with lighter shades of blue. Average annual accumulated precipitation is shown with the black dashed line. 

The winter was marked by near normal precipitation, with the heaviest rain in February and the first half of April. It has been *exceptionally dry* since late April. Only 109 mm of rain has fallen since April 24. On average, the lower Capilano Watershed typically sees around 280 mm of rain in May-June-July. 

We'll take a closer look at drought in the next section. 

In [27]:
alt.data_transformers.disable_max_rows()

title = alt.TitleParams(
   text='Lower Capilano Watershed',
   subtitle="Cummulative Precipitation (2003-2023)",
   anchor='middle',
   fontSize=14,
   fontWeight='bold')


background = alt.Chart(temp[temp['year'] != 2023], title=title).mark_line(opacity=0.3).encode(
    alt.X('monthdate(date):T', title=None),
    alt.Y('rain_cum_yr:Q', title='Cummulative Precipitation (mm)'),
    alt.Color('year:N', legend=None, scale=alt.Scale(scheme= 'blues'))
)


year_2023 = alt.Chart(temp[temp['year'] == 2023]).mark_line(color= "red", size= 3).encode(
    alt.X('monthdate(date):T', title=None),
    alt.Y('rain_cum_yr:Q', title='Cummulative Precipitation (mm)')
)

year_2022 = alt.Chart(temp[temp['year'] == 2022]).mark_line(color= "darkblue", opacity=0.7).encode(
    alt.X('monthdate(date):T', title=None),
    alt.Y('rain_cum_yr:Q', title='Cummulative Precipitation (mm)')
)

mean = alt.Chart(temp).mark_line(color= "black", opacity=0.7, strokeDash=[4, 2]).encode(
    alt.X('monthdate(date):T', title=None),
    alt.Y('mean(rain_cum_yr)', title='Cummulative Precipitation (mm)')
)

year_2023 + year_2022 + mean + background.properties(width=600).interactive()

alt.LayerChart(...)

```{admonition} Dry Spells!
**33 days** (May 7 - June 9), and **25 days** (June 23 - July 18)

*Note: Only 0.5 mm of rain fell in 32 days between June 22 and July 24*
```